# Install and import the useful libraries that we use

In [ ]:
%%bash

pip install --upgrade pip
pip install git+https://github.com/deepset-ai/haystack.git@3a2714e7c877c8ee8b886f2ae888e74968de8f25#egg=farm-haystack[colab]
python -m spacy download en 
python -m spacy download en_core_web_lg

In [2]:
import nltk, uuid, re, json, en_core_web_lg, time, logging, torch, multiprocessing, haystack, os, pickle
from nltk import word_tokenize
from tqdm import tqdm
import pandas as pd
import numpy as np

nltk.download('punkt')
path='./'

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


In [3]:
from subprocess import Popen, PIPE, STDOUT
from typing import List, Optional, Dict, Any, Union, Callable
from pathlib import Path
from collections import defaultdict
from time import perf_counter
from haystack.modeling.data_handler.data_silo import DataSilo, DistillationDataSilo
from haystack.modeling.data_handler.processor import SquadProcessor, Processor
from haystack.modeling.data_handler.dataloader import NamedDataLoader
from haystack.modeling.data_handler.inputs import QAInput, Question
from haystack.modeling.infer import QAInferencer
from haystack.modeling.model.optimization import initialize_optimizer
from haystack.modeling.model.predictions import QAPred, QACandidate
from haystack.modeling.model.adaptive_model import AdaptiveModel
from haystack.modeling.training import Trainer, DistillationTrainer, TinyBERTDistillationTrainer
from haystack.modeling.evaluation import Evaluator, metrics
from haystack.modeling.utils import set_all_seeds, initialize_device_settings
from haystack.schema import Document, Answer, Span
from haystack.document_stores.base import BaseDocumentStore
from haystack.document_stores import ElasticsearchDocumentStore
from haystack.nodes.reader.base import BaseReader
from haystack.nodes.retriever.sparse import TfidfRetriever
from haystack.nodes import FARMReader, TransformersReader, PreProcessor
from haystack.pipelines import ExtractiveQAPipeline
from haystack.utils import print_answers

In [4]:
import locale
locale.getpreferredencoding = lambda: "UTF-8" # run these codes to solve "A UTF-8 locale is required." issue

# Read Data and Transform it into SQUAD format

In [ ]:
def loadObj(filename):
    filehandler = open(filename, 'rb') 
    obj=pickle.load(filehandler)    
    filehandler.close()
    return obj
def saveObj(ob,filename):
    filehandler = open(filename, 'wb') 
    pickle.dump(ob, filehandler)
    filehandler.close()

In [ ]:
GT = loadObj(path+"GTv6.obj")

In [ ]:
def answer_start(story_text, answer_text):
    if answer_text:
        return story_text.find(str(answer_text))
    else:
        return -1

In [ ]:
def gt_to_squad(gt=GT):
    gt.loc[:,'question'] = gt.Q
    gt.loc[:,'story_text'] = gt.C
    gt.loc[:,'answer_text'] = gt.A.apply(lambda x: str(x))
    gt.loc[:,'answer_start'] = gt[['C', 'A']].apply(lambda x: answer_start(*x), axis=1)
    gt.loc[:,'id'] = gt.Id.apply(lambda x: str(uuid.uuid4().hex))
    gt = gt[['id', 'story_text', 'question', 'answer_text', 'answer_start']].copy()
    gt=gt[gt['answer_start']!=-1].copy()
    print(gt.shape)
    gt_json = gt.to_json(orient='records')
    gt_json = json.loads(gt_json)

    data = []

    for gt_example in gt_json:
        question_text = gt_example['question']
        context = gt_example['story_text']

        para = {'context': context, 'qas': [{'question': question_text, 'answers': []}]}
        data.append({'paragraphs': [para]})
        qa = para['qas'][0]
        qa['id'] = gt_example['id']
        qa['is_impossible'] = True

        if gt_example['answer_start'] != -1:
            ans_string = gt_example['answer_text']
            index = gt_example['answer_start']
            qa['answers'].append({'text': ans_string, 'answer_start': index})
            qa['is_impossible'] = False

    gt_as_squad = {'data': data, 'version': '2.0'}

    return gt_as_squad

In [ ]:
jsonf=gt_to_squad(GT)

(374, 5)


In [ ]:
with open(path+'gt.json', 'w', encoding='utf-8') as outfile:
  json.dump(jsonf, outfile, indent=2, sort_keys=True, ensure_ascii=False)

In [ ]:
model_list=[
            "deepset/roberta-base-squad2",
            "deepset/bert-large-uncased-whole-word-masking-squad2",
            "distilbert-base-cased-distilled-squad",
            "ahotrod/albert_xxlargev1_squad2_512",
            "deepset/electra-base-squad2",
            "deepset/minilm-uncased-squad2"
]

In [ ]:
def eval_on_file(
    self, data_dir: Union[Path, str], test_filename: str, device: Optional[Union[str, torch.device]] = None
):
    
    if device is None:
        device = self.devices[0]
    else:
        device = torch.device(device)

    eval_processor = SquadProcessor(
        tokenizer=self.inferencer.processor.tokenizer,
        max_seq_len=self.inferencer.processor.max_seq_len,
        label_list=self.inferencer.processor.tasks["question_answering"]["label_list"],
        metric=self.inferencer.processor.tasks["question_answering"]["metric"],
        train_filename=None,
        dev_filename=None,
        dev_split=0,
        test_filename=test_filename,
        data_dir=Path(data_dir),
    )

    data_silo = DataSilo(processor=eval_processor, batch_size=self.inferencer.batch_size, distributed=False)
    data_loader = data_silo.get_data_loader("test")

    evaluator = Evaluator(data_loader=data_loader, tasks=eval_processor.tasks, device=device)

    eval_results = evaluator.eval(self.inferencer.model,return_preds_and_labels=True)
    results = {
        "EM": eval_results[0]["EM"],
        "f1": eval_results[0]["f1"],
        "top_n_accuracy": eval_results[0]["top_n_accuracy"],
    }
    return results, eval_results

In [ ]:
def top_n_accuracy(preds, labels,n):
    answer_in_top_n = []
    n_questions = len(preds)
    for i in range(n_questions):
        f1_score = 0
        current_preds = preds[i][0]
        for idx, pred in enumerate(current_preds[:n]):
            f1_score = max([metrics.squad_f1_single(current_preds, label, pred_idx=idx) for label in labels[i]])
            if f1_score:
                break
        if f1_score:
            answer_in_top_n.append(1)
        else:
            answer_in_top_n.append(0)
    return np.mean(answer_in_top_n)

#Elastic Search Server

In [5]:
! wget https://artifacts.elastic.co/downloads/elasticsearch/elasticsearch-7.9.2-linux-x86_64.tar.gz -q
! tar -xzf elasticsearch-7.9.2-linux-x86_64.tar.gz
! chown -R daemon:daemon elasticsearch-7.9.2

# start (and restart) elastic server
TO RUN AGAIN WHEN ConnectionError IS FACED

In [6]:
es_server = Popen(
    ["elasticsearch-7.9.2/bin/elasticsearch"], stdout=PIPE, stderr=STDOUT, preexec_fn=lambda: os.setuid(1)  # as daemon
)
# wait until ES has started
! sleep 40

# prepare data and define metrics

In [8]:
# Connect to Elasticsearch
document_store = ElasticsearchDocumentStore(
    host="localhost",
    username="",
    password="",
    index="doc_index",
    label_index="label_index",
    embedding_field="emb",
    embedding_dim=768,
    excluded_meta_data=["emb"],
)
#document_store = InMemoryDocumentStore()

In [ ]:
preprocessor = PreProcessor(
    split_length=200,
    split_overlap=0,
    split_respect_sentence_boundary=False,
    clean_empty_lines=False,
    clean_whitespace=False,
)
document_store.delete_documents(index="doc_index")
document_store.delete_documents(index="label_index")

# The add_eval_data() method converts the given dataset in json format into Haystack document and label objects. Those objects are then indexed in their respective document and label index in the document store. The method can be used with any dataset in SQuAD format.
document_store.add_eval_data(
    filename=path+"gt.json",
    doc_index="doc_index",
    label_index="label_index",
    preprocessor=preprocessor,
)


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


Preprocessing:   0%|          | 0/1 [00:00<?, ?docs/s]

Preprocessing:   0%|          | 0/1 [00:00<?, ?docs/s]

Preprocessing:   0%|          | 0/1 [00:00<?, ?docs/s]

Preprocessing:   0%|          | 0/1 [00:00<?, ?docs/s]

...

Preprocessing:   0%|          | 0/1 [00:00<?, ?docs/s]

Preprocessing:   0%|          | 0/1 [00:00<?, ?docs/s]

Preprocessing:   0%|          | 0/1 [00:00<?, ?docs/s]

Preprocessing:   0%|          | 0/1 [00:00<?, ?docs/s]

Preprocessing:   0%|          | 0/1 [00:00<?, ?docs/s]

In [ ]:
from haystack.nodes import BM25Retriever
retriever = BM25Retriever(document_store=document_store)
eval_labels = document_store.get_all_labels_aggregated(drop_negative_labels=True, drop_no_answers=True)

In [ ]:
nlp = en_core_web_lg.load()
def SpacySim(s1,s2):
  return nlp(s1).similarity(nlp(s2))

In [ ]:
def similarityAccuracyV2(rdf):
  scores=[]
  for i in tqdm(rdf[rdf['rank']==1].index):
    scores.append(SpacySim(rdf['gold_answers'][i][0],rdf['answer'][i]))
  return np.mean(scores)

In [ ]:
def similarityAccuracy(rdf,threshold=0.5):
  corrects=[]
  for i in tqdm(rdf[rdf['rank']==1].index):
    if SpacySim(rdf['gold_answers'][i][0],rdf['answer'][i])>threshold:
      corrects.append(1)
    else:
      corrects.append(0)
  return np.mean(corrects)

In [ ]:
def getScores(advanced_eval_result,preds,labels,ext):
  rdf=advanced_eval_result['Reader']
  rdf.reset_index(drop=True, inplace =True)
  ms=advanced_eval_result.calculate_metrics()
  em = ms['Reader']['exact_match']
  f1 = ms['Reader']['f1']
  a =[top_n_accuracy(preds,labels,n) for n in range(1,5)]
  sa=similarityAccuracyV2(rdf)
  return '\t'.join([str(s) for s in [sa,em,f1]+a+[ext]])

In [ ]:
def getScoresLite(reader_eval_results,ext):
  em = reader_eval_results['EM']
  f1 = reader_eval_results['f1']
  a = reader_eval_results['top_n_accuracy']
  print('\t'.join([str(s) for s in [em,f1,a,ext]]))
  return '\t'.join([str(s) for s in [em,f1,a,ext]])

# Run the pipeline

In [ ]:
results={}
for model in model_list:
  start_time = time.time()
  reader = FARMReader(model, top_k_per_candidate=10, return_no_answer=False,use_gpu=True, progress_bar=False)
  pipeline = ExtractiveQAPipeline(reader=reader,retriever=retriever)
  advanced_eval_result = pipeline.eval(labels=eval_labels, sas_model_name_or_path="cross-encoder/stsb-roberta-large", add_isolated_node_eval=True)
  reader_eval_results,evalresults = eval_on_file(reader,path, "gt.json",device=torch.device('cuda'))
  preds,labels=evalresults[0]['preds'],evalresults[0]['labels']
  print(model)
  ext = time.time() - start_time
  results[model] = getScores(advanced_eval_result,preds,labels,ext)

In [ ]:
print('\t'.join(['Model','SA','EM','PM','Execution time']))
for model in model_list:
  print(model+"\t"+results[model])

# Show example

This selects a random question and provide the selected answers using Roberta

In [ ]:
import random
random_question = random.choice(GT.Q)
print(random_question)

In [ ]:
reader = FARMReader(model_list[0], top_k_per_candidate=10, return_no_answer=False,use_gpu=True, progress_bar=False)
pipeline = ExtractiveQAPipeline(reader=reader,retriever=retriever)
prediction = pipeline.run(query=random_question)

In [ ]:
print_answers(prediction, details="minimum")